In [1]:
import os
import sys
import zipfile
import pandas as pd
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt

%matplotlib inline

sys.path.append('../')
from src.data_preprocess import DataPreprocessor

pd.set_option('display.max_colwidth', 2000)

%load_ext autoreload
%autoreload 2

In [4]:
data_folder = "//fsfshadoopstage/hadoop_stage/PEE_joint/NUS_modules/CS5228/CS5228/input"
if len(os.listdir(data_folder))<2:
    if not os.listdir(data_folder):
        !kaggle competitions download -c cs5228-2022-semester-1-final-group-project -p ../input
    Dataset = "cs5228-2022-semester-1-final-group-project"
    with zipfile.ZipFile(f"{data_folder}/{Dataset}.zip","r") as z:
        z.extractall("../input")

In [5]:
for dirname, _, filenames in os.walk('../input'):
    for filename in filenames:
        if filename.endswith('csv'):
            print(os.path.join(dirname, filename))

../input\example-submission.csv
../input\test.csv
../input\train.csv
../input\auxiliary-data\sg-commerical-centres.csv
../input\auxiliary-data\sg-mrt-stations.csv
../input\auxiliary-data\sg-primary-schools.csv
../input\auxiliary-data\sg-secondary-schools.csv
../input\auxiliary-data\sg-shopping-malls.csv
../input\auxiliary-data\sg-subzones.csv


In [37]:
train_df = pd.read_csv('../input/train.csv').reset_index()
train_df.head(2)

index  listing_id                                               title  \
0      0      122881           hdb flat for sale in 866 yishun street 81   
1      1      259374  hdb flat for sale in 506b serangoon north avenue 4   

                              address         property_name property_type  \
0            sembawang / yishun (d27)  866 yishun street 81   hdb 4 rooms   
1  hougang / punggol / sengkang (d19)  hdb-serangoon estate           hdb   

              tenure  built_year  num_beds  num_baths  ...   furnishing  \
0                NaN      1988.0       3.0        2.0  ...  unspecified   
1  99-year leasehold      1992.0       4.0        2.0  ...  unspecified   

  available_unit_types total_num_units  \
0                  NaN           116.0   
1  1, 2, 3, 4, 5, 6 br             NaN   

                                                            property_details_url  \
0  https://www.99.co/singapore/hdb/866-yishun-street-81-adxawp85buupmsq7gwdjverc   
1   https://www.99.co/singapore/hdb/hdbserangoon-estate-demrpm6ryc3l9buf846erprb   

        lat         lng  elevation          subzone  planning_area     price  
0  1.414399  103.837196          0     yishun south         yishun  514500.0  
1  1.372597  103.875625          0  serangoon north      serangoon  995400.0  

[2 rows x 22 columns]

In [38]:
# print(train_df.shape)
# display(train_df.isnull().sum())
# display(train_df.info())

In [39]:
# train_df.isnull().sum()

In [40]:
# fig = px.violin(train_df, y="price", box=True, points="all", hover_data=train_df.columns)
# fig.show()

In [41]:
train_df_clean = DataPreprocessor.remove_price_outlier(train_df)
# fig = px.violin(train_df_clean, y="price", box=True, points="all", hover_data=train_df.columns)
# fig.show()

In [42]:
train_df_clean = DataPreprocessor.preprocess_title(train_df_clean)
display(train_df_clean.loc[:, ['title_property_type','property_type']].head(3))
display(train_df_clean.loc[:, ['title_n_beds','num_beds']].head(3)) ## if hdb flat,can get from property_type
display(train_df_clean.loc[:, ['title_address','address']].head(3))

title_property_type property_type
0            hdb flat   hdb 4 rooms
1            hdb flat           hdb
2               condo         condo

title_n_beds  num_beds
0     hdb flat       3.0
1     hdb flat       4.0
2            4       4.0

title_address                             address
0           866 yishun street 81            sembawang / yishun (d27)
1  506b serangoon north avenue 4  hougang / punggol / sengkang (d19)
2                     meyerhouse                      128 meyer road

In [45]:
display(train_df_clean.loc[:, ['title_property_type','property_type', 'title_n_beds','num_beds', 'title_address','address']])

title_property_type property_type title_n_beds  num_beds  \
0                hdb flat   hdb 4 rooms     hdb flat       3.0   
1                hdb flat           hdb     hdb flat       4.0   
2                   condo         condo            4       4.0   
3                   condo         Condo            3       3.0   
4                   condo         condo            2       2.0   
...                   ...           ...          ...       ...   
20249               condo         condo            2       2.0   
20250               condo         Condo            2       2.0   
20251               condo         condo            4       4.0   
20252            hdb flat   hdb 5 rooms     hdb flat       3.0   
20253               condo         condo            4       4.0   

                       title_address                             address  
0               866 yishun street 81            sembawang / yishun (d27)  
1      506b serangoon north avenue 4  hougang / punggol / sengkang (d19)  
2                         meyerhouse                      128 meyer road  
3                       leedon green                   26 leedon heights  
4                         one bernam                     1 bernam street  
...                              ...                                 ...  
20249                  lentor modern                      lentor central  
20250                           mori                 223 guillemard road  
20251      pullman residences newton                     18 dunearn road  
20252        691d woodlands drive 73         admiralty / woodlands (d25)  
20253      pullman residences newton                     18 dunearn road  

[20252 rows x 6 columns]

## lat & lng

In [47]:
train_df_clean['lat'] = train_df_clean['lat'].astype(float)
train_df_clean['lng'] = train_df_clean['lng'].astype(float)
# fig = px.histogram(train_df_clean[(zscore(train_df_clean['lng']) > -1) & (zscore(train_df_clean['lng']) < 1)], x='lng')
fig = px.histogram(train_df_clean, x='lat')
fig.show()
fig = px.histogram(train_df_clean, x='lng')
fig.show()

In [56]:
fig = px.scatter(train_df, x='lat', y='lng')
fig.show()

In [53]:
train_df_clean = DataPreprocessor.preprocess_lat_lng(train_df_clean)

In [55]:
fig = px.scatter(train_df_clean, x='lat', y='lng')
fig.show()

In [52]:
def fu(sub_df):
    if((sub_df[~((sub_df['lat'] > 1) & (sub_df['lat'] < 2))].shape[0]>0) 
       & (sub_df[~((sub_df['lng'] > 103) & (sub_df['lng'] < 105))].shape[0]>0)):
        display(sub_df[["address", "title_address", 'lat', 'lng']].drop_duplicates())
train_df_clean.groupby('address').apply(fu)

address title_address        lat         lng
30  1 tessensohn road          1953  14.484814  121.023232

address  title_address        lat        lng
86  15 farrer drive  pollen & bleu  69.486768  20.184434

address  title_address        lat        lng
2765  17 farrer drive  pollen & bleu  69.486768  20.184434

address title_address        lat        lng
4792  38 lorong 32 geylang          ness  38.942776 -77.065364

address title_address        lat         lng
6393  5 jalan mutiara            m5  14.484814  121.023232

Empty DataFrame
Columns: []
Index: []